# Illustration of DFT predict

In [1]:
import sys
import itertools
import time
import numpy
import operator

## Baseline visibilities

Generate baseline coordinates for an observation with SKA1 LOW over 6 hours, with a visibility recorded every hour. The phase center is fixed at a declination of 45 degrees. We assume that the imaged sky stays at that position over the course of the observation.

In [2]:
def xyz_at_latitude(local_xyz, lat):
    x, y, z = numpy.hsplit(local_xyz, 3)
    lat2 = numpy.pi / 2 - lat
    y2 = -z * numpy.sin(lat2) + y * numpy.cos(lat2)
    z2 = z * numpy.cos(lat2) + y * numpy.sin(lat2)
    return numpy.hstack([x, y2, z2])

# Telescope
xyz = xyz_at_latitude(numpy.genfromtxt("../../data/configurations/LOWBD2.csv", delimiter=','), numpy.radians(-26.7))
nbl = len(xyz) * (len(xyz) - 1) // 2
# Declination, hour range range, wave lengths
dec = numpy.radians(45)
ha_range = numpy.arange(numpy.radians(0),
                        numpy.radians(90),
                        numpy.radians(90 / 6))
wls = 1 / numpy.arange(1 / 6, 1, 1 / 12)
nvis = len(wls) * len(ha_range) * nbl
# Grid of sources
B, l, m = numpy.transpose([ (1, 0.01 * l,  0.01 * m) for l, m in itertools.product(range(-4, 3), range(-4, 3)) ])
# Statistics
print("{} channels, {} time steps, {} baselines, {} sources".format(len(wls),len(ha_range), nbl, len(B)))
print(" => {} visibilities, {} flops".format(nvis, 4 * nvis * len(B)))

11 channels, 6 time steps, 130816 baselines, 49 sources
 => 8633856 visibilities, 1692235776 flops


In [3]:
def xyz_to_uvw(xyz, ha, dec):
    x, y, z = numpy.hsplit(xyz, 3)
    u = x * numpy.cos(ha) - y * numpy.sin(ha)
    v0 = x * numpy.sin(ha) + y * numpy.cos(ha)
    w = z * numpy.sin(dec) - v0 * numpy.cos(dec)
    v = z * numpy.cos(dec) + v0 * numpy.sin(dec)
    return numpy.hstack([u, v, w])
def baselines(ants_uvw):
    return numpy.array([ ants_uvw[j] - ants_uvw[i]
                         for i, j in itertools.combinations(range(ants_uvw.shape[0]), 2) ])
def xyz_to_baselines(ants_xyz, ha_range, dec):
    return numpy.concatenate([baselines(xyz_to_uvw(ants_xyz, hax, dec)) for hax in ha_range])
def simulate_point(dist_uvw, l, m):
    s = numpy.array([l, m, numpy.sqrt(1 - l ** 2 - m ** 2) - 1.0])
    return numpy.exp((-2j * numpy.pi) * numpy.dot(dist_uvw, s))

First the direct way, for comparison:

In [4]:
uvw = xyz_to_baselines(xyz, ha_range, dec)
t = time.time()
vis = numpy.hstack([ numpy.sum(B * simulate_point(uvw / wl, l, m), axis=1) for wl in wls ])
print("Took {:.3f}s ({} vis/s)".format(time.time() - t, len(vis) / (time.time() - t)))

Took 41.439s (208351.99320422887 vis/s)


If we assume some locality in frequency we can exploit
$$e^{-2\pi j (f_0 + \Delta f) \big((u_a - u_b) l + (v_a - v_b) m + (w_a - w_b) n\big)} = 
e^{-2\pi j f_0  \big((u_a - u_b) l + (v_a - v_b) m + (w_a - w_b) n\big)}
e^{-2\pi j \Delta f  \big((u_a - u_b) l + (v_a - v_b) m + (w_a - w_b) n\big)}$$
as follows:

In [5]:
vis2 = numpy.empty(nbl * len(wls) * len(ha_range), dtype=complex)
fc0 = 1 / wls[0] # Frequency divided by c
dfc = 1 / wls[1] - 1 / wls[0] # Assumed to be constant
t = time.time()
vis_f0 = B * simulate_point(uvw * fc0, l, m)
vis_df = simulate_point(uvw * dfc, l, m)
t2 = time.time()
for i, vis_slice in enumerate(numpy.split(vis2, len(wls))):
    if i > 0: vis_f0 *= vis_df
    vis_slice[:] = numpy.sum(vis_f0, axis=1)
    
print("Took {:.3f}s+{:.3f}s={:.3f}s ({} vis/s)".format(t2-t, time.time() - t2, time.time() - t,
                                                       len(vis) / (time.time() - t)))
print("RMSE: {}".format(numpy.sqrt(numpy.average(numpy.abs(vis-vis2)**2))))

Took 7.080s+2.248s=9.328s (925579.5286384724 vis/s)
RMSE: 1.4404394266059432e-12


Finally if we have baseline locality we can use
\begin{align*}
e^{-2\pi j (f_0 + \Delta f) \big((u_a - u_b) l + (v_a - v_b) m + (w_a - w_b) n\big)} = 
e^{-2\pi j (f_0 + \Delta f) \big(u_a l + v_a  m + w_a n\big)}
e^{2\pi j (f_0 + \Delta f) \big(u_b l + v_b m + w_b n\big)}
\end{align*}
as suggested by Salvini et al:

In [6]:
vis3 = numpy.empty(nbl * len(wls) * len(ha_range), dtype=complex)
t = time.time()
for wl, vis_slice in zip(wls, numpy.split(vis3, len(wls))):
    for ha, vis_slice2 in zip(ha_range, numpy.split(vis_slice, len(ha_range))):
        uvw_f = xyz_to_uvw(xyz, ha, dec) / wl
        Z = B * simulate_point(uvw_f, l,m)
        # Note that this calculates both halves of the matrix, which is redundant
        V = numpy.dot(Z.conj(), Z.T)
        vis_slice2[:] = V[numpy.triu_indices(len(xyz), 1)]
print("Took {:.3f}s ({} vis/s)".format(time.time() - t, len(vis2) / (time.time() - t)))
print("RMSE: {}".format(numpy.sqrt(numpy.average(numpy.abs(vis-vis3)**2))))

Took 0.768s (11244920.025569582 vis/s)
RMSE: 1.4389095196990204e-12


Note that this does about double the operations needed, and could be combined with the frequency-axis optimisation as well.

## On-grid visibilities

Something else that can be done efficiently is to DFT to a grid. Speculation here is that this could be degridded from - assuming we apply a grid correction to the sources. This would likely still be an order of magnitude cheaper than solving the DFT for the visibilities directly, so this might be a solution for exceptionally bright sources that do not align well with the image grid.

In [7]:
du = dv = 71
u, v = numpy.meshgrid(numpy.arange(numpy.min(uvw) / wls[0], numpy.max(uvw), du),
                      numpy.arange(numpy.min(uvw) / wls[0], numpy.max(uvw), dv))
w = numpy.zeros_like(u)
uvw_grid = numpy.transpose([u,v,w]).reshape(u.size, 3)
print("{} grid points".format(len(uvw_grid)))

1490841 grid points


In [8]:
t = time.time()
vis_grid = numpy.sum(B * simulate_point(uvw_grid, l, m), axis=1)
print("Took {:.3f}s ({} vis/s)".format(time.time() - t, len(vis_grid) / (time.time() - t)))

Took 7.403s (201376.344150691 vis/s)


Here we decompose
\begin{align*}
e^{-2\pi j \frac fc \big((u_0 + i_u \Delta u) l + (v_0 + i_v \Delta v) m + w_0 n\big)} = 
e^{-2\pi j \frac fc (u_0 l + v_0 m + w_0 n)}
e^{-2\pi j \frac fc i_u \Delta u l} e^{-2\pi j \frac fc i_v \Delta v m}
\end{align*}
This means that we can derive everything from just 3 sine-cosine pairs per source:

In [9]:
t = time.time()
vis00 = simulate_point(uvw_grid[0], l, m)
vis_du = simulate_point(numpy.array([du,0,0]), l, m)
vis_dus = vis00 * numpy.vstack([vis_du ** i for i in range(len(u))])
vis_dv = simulate_point(numpy.array([0,dv,0]), l, m)
vis_dvs = numpy.vstack([vis_dv ** i for i in range(len(v))])
vis_grid2 = numpy.dot(vis_dus, vis_dvs.T).flatten()
print("Took {:.3f}s ({} vis/s)".format(time.time() - t, len(vis_grid) / (time.time() - t)))
print("RMSE: {}".format(numpy.sqrt(numpy.average(numpy.abs(vis_grid-vis_grid2)**2))))

Took 0.082s (18069707.55658559 vis/s)
RMSE: 7.556124151737702e-12
